# Starbucks Capstone Challenge

### Introduction

This data set contains simulated data that mimics customer behavior on the Starbucks rewards mobile app. Once every few days, Starbucks sends out an offer to users of the mobile app. An offer can be merely an advertisement for a drink or an actual offer such as a discount or BOGO (buy one get one free). Some users might not receive any offer during certain weeks. 

Not all users receive the same offer, and that is the challenge to solve with this data set.

Your task is to combine transaction, demographic and offer data to determine which demographic groups respond best to which offer type. This data set is a simplified version of the real Starbucks app because the underlying simulator only has one product whereas Starbucks actually sells dozens of products.

Every offer has a validity period before the offer expires. As an example, a BOGO offer might be valid for only 5 days. You'll see in the data set that informational offers have a validity period even though these ads are merely providing information about a product; for example, if an informational offer has 7 days of validity, you can assume the customer is feeling the influence of the offer for 7 days after receiving the advertisement.

You'll be given transactional data showing user purchases made on the app including the timestamp of purchase and the amount of money spent on a purchase. This transactional data also has a record for each offer that a user receives as well as a record for when a user actually views the offer. There are also records for when a user completes an offer. 

Keep in mind as well that someone using the app might make a purchase through the app without having received an offer or seen an offer.

### Example

To give an example, a user could receive a discount offer buy 10 dollars get 2 off on Monday. The offer is valid for 10 days from receipt. If the customer accumulates at least 10 dollars in purchases during the validity period, the customer completes the offer.

However, there are a few things to watch out for in this data set. Customers do not opt into the offers that they receive; in other words, a user can receive an offer, never actually view the offer, and still complete the offer. For example, a user might receive the "buy 10 dollars get 2 dollars off offer", but the user never opens the offer during the 10 day validity period. The customer spends 15 dollars during those ten days. There will be an offer completion record in the data set; however, the customer was not influenced by the offer because the customer never viewed the offer.

### Cleaning

This makes data cleaning especially important and tricky.

You'll also want to take into account that some demographic groups will make purchases even if they don't receive an offer. From a business perspective, if a customer is going to make a 10 dollar purchase without an offer anyway, you wouldn't want to send a buy 10 dollars get 2 dollars off offer. You'll want to try to assess what a certain demographic group will buy when not receiving any offers.

### Final Advice

Because this is a capstone project, you are free to analyze the data any way you see fit. For example, you could build a machine learning model that predicts how much someone will spend based on demographics and offer type. Or you could build a model that predicts whether or not someone will respond to an offer. Or, you don't need to build a machine learning model at all. You could develop a set of heuristics that determine what offer you should send to each customer (i.e., 75 percent of women customers who were 35 years old responded to offer A vs 40 percent from the same demographic to offer B, so send offer A).

# Data Sets

The data is contained in three files:

* portfolio.json - containing offer ids and meta data about each offer (duration, type, etc.)
* profile.json - demographic data for each customer
* transcript.json - records for transactions, offers received, offers viewed, and offers completed

Here is the schema and explanation of each variable in the files:

**portfolio.json**
* id (string) - offer id
* offer_type (string) - type of offer ie BOGO, discount, informational
* difficulty (int) - minimum required spend to complete an offer
* reward (int) - reward given for completing an offer
* duration (int) - time for offer to be open, in days
* channels (list of strings)

**profile.json**
* age (int) - age of the customer 
* became_member_on (int) - date when customer created an app account
* gender (str) - gender of the customer (note some entries contain 'O' for other rather than M or F)
* id (str) - customer id
* income (float) - customer's income

**transcript.json**
* event (str) - record description (ie transaction, offer received, offer viewed, etc.)
* person (str) - customer id
* time (int) - time in hours since start of test. The data begins at time t=0
* value - (dict of strings) - either an offer id or transaction amount depending on the record

**Note:** If you are using the workspace, you will need to go to the terminal and run the command `conda update pandas` before reading in the files. This is because the version of pandas in the workspace cannot read in the transcript.json file correctly, but the newest version of pandas can. You can access the termnal from the orange icon in the top left of this notebook.  

You can see how to access the terminal and how the install works using the two images below.  First you need to access the terminal:

<img src="pic1.png"/>

Then you will want to run the above command:

<img src="pic2.png"/>

Finally, when you enter back into the notebook (use the jupyter icon again), you should be able to run the below cell without any errors.

In [36]:
import pandas as pd
import numpy as np
import math
import json
from tqdm import tqdm
import plotly.express as px
%matplotlib inline

# read in the json files
portfolio = pd.read_json('data/portfolio.json', orient='records', lines=True)
profile = pd.read_json('data/profile.json', orient='records', lines=True)
transcript = pd.read_json('data/transcript.json', orient='records', lines=True)

In [3]:
portfolio

reward                      channels  difficulty  duration     offer_type  \
0      10       [email, mobile, social]          10         7           bogo   
1      10  [web, email, mobile, social]          10         5           bogo   
2       0          [web, email, mobile]           0         4  informational   
3       5          [web, email, mobile]           5         7           bogo   
4       5                  [web, email]          20        10       discount   
5       3  [web, email, mobile, social]           7         7       discount   
6       2  [web, email, mobile, social]          10        10       discount   
7       0       [email, mobile, social]           0         3  informational   
8       5  [web, email, mobile, social]           5         5           bogo   
9       2          [web, email, mobile]          10         7       discount   

                              offer  
0  ae264e3637204a6fb9bb56bc8210ddfd  
1  4d5c57ea9a6940dd891ad53e9dbe8da0  
2  3f207df678b143eea3cee63160fa8bed  
3  9b98b8c7a33c4b65b9aebfe6a799e6d9  
4  0b1e1539f2cc45b7b9fa7c272da2e1d7  
5  2298d6c36e964ae4a3e7e9706d1fb8c2  
6  fafdcd668e3743c1bb461111dcafc2a4  
7  5a8bc65990b245e5a138643cd4eb9837  
8  f19421c1d4aa40978ebb69ca19b0e20d  
9  2906b810c7d4411798c6938adc9daaa5

In [2]:
portfolio.rename(columns={'id': 'offer'}, inplace=True)

In [4]:
for channel in ['email', 'mobile', 'social', 'web']:
    portfolio[channel] = portfolio['channels'].apply(lambda row: 1 if (channel in row) else 0)
# df.columns = ['team_{}'.format(x+1) for x in df.columns]

In [5]:
portfolio

reward                      channels  difficulty  duration     offer_type  \
0      10       [email, mobile, social]          10         7           bogo   
1      10  [web, email, mobile, social]          10         5           bogo   
2       0          [web, email, mobile]           0         4  informational   
3       5          [web, email, mobile]           5         7           bogo   
4       5                  [web, email]          20        10       discount   
5       3  [web, email, mobile, social]           7         7       discount   
6       2  [web, email, mobile, social]          10        10       discount   
7       0       [email, mobile, social]           0         3  informational   
8       5  [web, email, mobile, social]           5         5           bogo   
9       2          [web, email, mobile]          10         7       discount   

                              offer  email  mobile  social  web  
0  ae264e3637204a6fb9bb56bc8210ddfd      1       1       1    0  
1  4d5c57ea9a6940dd891ad53e9dbe8da0      1       1       1    1  
2  3f207df678b143eea3cee63160fa8bed      1       1       0    1  
3  9b98b8c7a33c4b65b9aebfe6a799e6d9      1       1       0    1  
4  0b1e1539f2cc45b7b9fa7c272da2e1d7      1       0       0    1  
5  2298d6c36e964ae4a3e7e9706d1fb8c2      1       1       1    1  
6  fafdcd668e3743c1bb461111dcafc2a4      1       1       1    1  
7  5a8bc65990b245e5a138643cd4eb9837      1       1       1    0  
8  f19421c1d4aa40978ebb69ca19b0e20d      1       1       1    1  
9  2906b810c7d4411798c6938adc9daaa5      1       1       0    1

In [6]:
profile

gender  age                                id  became_member_on  \
0       None  118  68be06ca386d4c31939f3a4f0e3dd783          20170212   
1          F   55  0610b486422d4921ae7d2bf64640c50b          20170715   
2       None  118  38fe809add3b4fcf9315a9694bb96ff5          20180712   
3          F   75  78afa995795e4d85b5d9ceeca43f5fef          20170509   
4       None  118  a03223e636434f42ac4c3df47e8bac43          20170804   
...      ...  ...                               ...               ...   
16995      F   45  6d5f3a774f3d4714ab0c092238f3a1d7          20180604   
16996      M   61  2cb4f97358b841b9a9773a7aa05a9d77          20180713   
16997      M   49  01d26f638c274aa0b965d24cefe3183f          20170126   
16998      F   83  9dc1421481194dcd9400aec7c9ae6366          20160307   
16999      F   62  e4052622e5ba45a8b96b59aba68cf068          20170722   

         income  
0           NaN  
1      112000.0  
2           NaN  
3      100000.0  
4           NaN  
...         ...  
16995   54000.0  
16996   72000.0  
16997   73000.0  
16998   50000.0  
16999   82000.0  

[17000 rows x 5 columns]

In [7]:
profile = profile[profile['income'].notnull()]
real_persons = profile.id.unique()

In [8]:
profile.rename(columns={'id': 'person'}, inplace=True)
profile

C:\Users\grego\Anaconda3\envs\venture\lib\site-packages\pandas\core\frame.py:4125: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return super().rename(


gender  age                            person  became_member_on  \
1          F   55  0610b486422d4921ae7d2bf64640c50b          20170715   
3          F   75  78afa995795e4d85b5d9ceeca43f5fef          20170509   
5          M   68  e2127556f4f64592b11af22de27a7932          20180426   
8          M   65  389bc3fa690240e798340f5a15918d5c          20180209   
12         M   58  2eeac8d8feae4a8cad5a6af0499a211d          20171111   
...      ...  ...                               ...               ...   
16995      F   45  6d5f3a774f3d4714ab0c092238f3a1d7          20180604   
16996      M   61  2cb4f97358b841b9a9773a7aa05a9d77          20180713   
16997      M   49  01d26f638c274aa0b965d24cefe3183f          20170126   
16998      F   83  9dc1421481194dcd9400aec7c9ae6366          20160307   
16999      F   62  e4052622e5ba45a8b96b59aba68cf068          20170722   

         income  
1      112000.0  
3      100000.0  
5       70000.0  
8       53000.0  
12      51000.0  
...         ...  
16995   54000.0  
16996   72000.0  
16997   73000.0  
16998   50000.0  
16999   82000.0  

[14825 rows x 5 columns]

In [ ]:
profile.hist()

In [ ]:
transcript

In [ ]:
transcript['event'].value_counts()

In [ ]:
persons_completed = transcript[transcript['event'] == 'offer completed']['person'].unique()
persons_viewed = transcript[transcript['event'] == 'offer viewed']['person'].unique()
persons_received = transcript[transcript['event'] == 'offer received']['person'].unique()

In [ ]:
transcript['person'].value_counts()

In [ ]:
transcript_train = transcript[transcript['person'].isin(persons_received) & transcript['person'].isin(persons_viewed)]
transcript_train = transcript_train[transcript_train['person'].isin(real_persons)]

In [ ]:
transcript_train['person'].value_counts()

In [ ]:
transcript_train

In [ ]:
transcript_offers = transcript_train.copy()
transcript_offers = transcript_offers[(transcript_offers['event'] == 'offer received') | (transcript_offers['event'] == 'offer viewed') | (transcript_offers['event'] == 'offer completed')]

In [ ]:
transcript_offers

In [ ]:
df_offers = pd.DataFrame(columns=['person', 'offer_received', 'offer_viewed', 'offer_completed', 'offer_id'])

In [71]:
offers_df = pd.DataFrame()
for person in tqdm(real_persons):
    df_aux = transcript_offers[transcript_offers['person'] == person]

    offers = dict()
    for line in range(len(df_aux)):
        if df_aux.iloc[line, df_aux.columns.get_loc('event')] == 'offer received':
            offers[df_aux.iloc[line, df_aux.columns.get_loc('value')].get('offer id')] = dict()
            offers[df_aux.iloc[line, df_aux.columns.get_loc('value')].get('offer id')]['person'] = person

            offers[df_aux.iloc[line, df_aux.columns.get_loc('value')].get('offer id')]['offer received'] = df_aux.iloc[line, df_aux.columns.get_loc('time')]
        elif df_aux.iloc[line, df_aux.columns.get_loc('event')] == 'offer viewed':
            offers[df_aux.iloc[line, df_aux.columns.get_loc('value')].get('offer id')]['offer viewed'] = df_aux.iloc[line, df_aux.columns.get_loc('time')]
        else:
            offers[df_aux.iloc[line, df_aux.columns.get_loc('value')]['offer_id']]['offer completed'] = df_aux.iloc[line, df_aux.columns.get_loc('time')]
            offers[df_aux.iloc[line, df_aux.columns.get_loc('value')]['offer_id']]['reward'] = df_aux.iloc[line, df_aux.columns.get_loc('value')]['reward']

    offers_df = offers_df.append(pd.DataFrame(offers).transpose())

100%|██████████| 14825/14825 [12:35<00:00, 19.63it/s]


In [73]:
offers_df['offer'] = offers_df.index
offers_df

person  \
9b98b8c7a33c4b65b9aebfe6a799e6d9  78afa995795e4d85b5d9ceeca43f5fef   
5a8bc65990b245e5a138643cd4eb9837  78afa995795e4d85b5d9ceeca43f5fef   
ae264e3637204a6fb9bb56bc8210ddfd  78afa995795e4d85b5d9ceeca43f5fef   
f19421c1d4aa40978ebb69ca19b0e20d  78afa995795e4d85b5d9ceeca43f5fef   
2906b810c7d4411798c6938adc9daaa5  e2127556f4f64592b11af22de27a7932   
...                                                            ...   
9b98b8c7a33c4b65b9aebfe6a799e6d9  9dc1421481194dcd9400aec7c9ae6366   
ae264e3637204a6fb9bb56bc8210ddfd  9dc1421481194dcd9400aec7c9ae6366   
2298d6c36e964ae4a3e7e9706d1fb8c2  e4052622e5ba45a8b96b59aba68cf068   
3f207df678b143eea3cee63160fa8bed  e4052622e5ba45a8b96b59aba68cf068   
f19421c1d4aa40978ebb69ca19b0e20d  e4052622e5ba45a8b96b59aba68cf068   

                                 offer received offer viewed offer completed  \
9b98b8c7a33c4b65b9aebfe6a799e6d9              0            6             132   
5a8bc65990b245e5a138643cd4eb9837            168          216             NaN   
ae264e3637204a6fb9bb56bc8210ddfd            408          408             510   
f19421c1d4aa40978ebb69ca19b0e20d            504          582             510   
2906b810c7d4411798c6938adc9daaa5              0           18             NaN   
...                                         ...          ...             ...   
9b98b8c7a33c4b65b9aebfe6a799e6d9            408          516             414   
ae264e3637204a6fb9bb56bc8210ddfd            576          624             594   
2298d6c36e964ae4a3e7e9706d1fb8c2              0            6              54   
3f207df678b143eea3cee63160fa8bed            576          NaN             NaN   
f19421c1d4aa40978ebb69ca19b0e20d            408          546             480   

                                 reward                             offer  
9b98b8c7a33c4b65b9aebfe6a799e6d9      5  9b98b8c7a33c4b65b9aebfe6a799e6d9  
5a8bc65990b245e5a138643cd4eb9837    NaN  5a8bc65990b245e5a138643cd4eb9837  
ae264e3637204a6fb9bb56bc8210ddfd     10  ae264e3637204a6fb9bb56bc8210ddfd  
f19421c1d4aa40978ebb69ca19b0e20d      5  f19421c1d4aa40978ebb69ca19b0e20d  
2906b810c7d4411798c6938adc9daaa5    NaN  2906b810c7d4411798c6938adc9daaa5  
...                                 ...                               ...  
9b98b8c7a33c4b65b9aebfe6a799e6d9      5  9b98b8c7a33c4b65b9aebfe6a799e6d9  
ae264e3637204a6fb9bb56bc8210ddfd     10  ae264e3637204a6fb9bb56bc8210ddfd  
2298d6c36e964ae4a3e7e9706d1fb8c2      3  2298d6c36e964ae4a3e7e9706d1fb8c2  
3f207df678b143eea3cee63160fa8bed    NaN  3f207df678b143eea3cee63160fa8bed  
f19421c1d4aa40978ebb69ca19b0e20d      5  f19421c1d4aa40978ebb69ca19b0e20d  

[54867 rows x 6 columns]

In [76]:
offers_df.to_csv("processed_data/offers_processed.csv", index=False)

In [20]:
offers_df = pd.read_csv("processed_data/offers_processed.csv")

In [21]:
offers_profile = pd.merge(offers_df, profile, on=['person'], how='left')

In [22]:
offers_profile_complete = pd.merge(offers_profile, portfolio, on=['offer'], how='left')
offers_profile_complete.drop(['channels'], inplace=True, axis=1)
offers_profile_complete

Unnamed: 0                            person  \
0      9b98b8c7a33c4b65b9aebfe6a799e6d9  78afa995795e4d85b5d9ceeca43f5fef   
1      5a8bc65990b245e5a138643cd4eb9837  78afa995795e4d85b5d9ceeca43f5fef   
2      ae264e3637204a6fb9bb56bc8210ddfd  78afa995795e4d85b5d9ceeca43f5fef   
3      f19421c1d4aa40978ebb69ca19b0e20d  78afa995795e4d85b5d9ceeca43f5fef   
4      2906b810c7d4411798c6938adc9daaa5  e2127556f4f64592b11af22de27a7932   
...                                 ...                               ...   
54862  9b98b8c7a33c4b65b9aebfe6a799e6d9  9dc1421481194dcd9400aec7c9ae6366   
54863  ae264e3637204a6fb9bb56bc8210ddfd  9dc1421481194dcd9400aec7c9ae6366   
54864  2298d6c36e964ae4a3e7e9706d1fb8c2  e4052622e5ba45a8b96b59aba68cf068   
54865  3f207df678b143eea3cee63160fa8bed  e4052622e5ba45a8b96b59aba68cf068   
54866  f19421c1d4aa40978ebb69ca19b0e20d  e4052622e5ba45a8b96b59aba68cf068   

       offer received  offer viewed  offer completed  reward_x  \
0                   0           6.0            132.0       5.0   
1                 168         216.0              NaN       NaN   
2                 408         408.0            510.0      10.0   
3                 504         582.0            510.0       5.0   
4                   0          18.0              NaN       NaN   
...               ...           ...              ...       ...   
54862             408         516.0            414.0       5.0   
54863             576         624.0            594.0      10.0   
54864               0           6.0             54.0       3.0   
54865             576           NaN              NaN       NaN   
54866             408         546.0            480.0       5.0   

                                  offer gender  age  became_member_on  \
0      9b98b8c7a33c4b65b9aebfe6a799e6d9      F   75          20170509   
1      5a8bc65990b245e5a138643cd4eb9837      F   75          20170509   
2      ae264e3637204a6fb9bb56bc8210ddfd      F   75          20170509   
3      f19421c1d4aa40978ebb69ca19b0e20d      F   75          20170509   
4      2906b810c7d4411798c6938adc9daaa5      M   68          20180426   
...                                 ...    ...  ...               ...   
54862  9b98b8c7a33c4b65b9aebfe6a799e6d9      F   83          20160307   
54863  ae264e3637204a6fb9bb56bc8210ddfd      F   83          20160307   
54864  2298d6c36e964ae4a3e7e9706d1fb8c2      F   62          20170722   
54865  3f207df678b143eea3cee63160fa8bed      F   62          20170722   
54866  f19421c1d4aa40978ebb69ca19b0e20d      F   62          20170722   

         income  reward_y  difficulty  duration     offer_type  email  mobile  \
0      100000.0         5           5         7           bogo      1       1   
1      100000.0         0           0         3  informational      1       1   
2      100000.0        10          10         7           bogo      1       1   
3      100000.0         5           5         5           bogo      1       1   
4       70000.0         2          10         7       discount      1       1   
...         ...       ...         ...       ...            ...    ...     ...   
54862   50000.0         5           5         7           bogo      1       1   
54863   50000.0        10          10         7           bogo      1       1   
54864   82000.0         3           7         7       discount      1       1   
54865   82000.0         0           0         4  informational      1       1   
54866   82000.0         5           5         5           bogo      1       1   

       social  web  
0           0    1  
1           1    0  
2           1    0  
3           1    1  
4           0    1  
...       ...  ...  
54862       0    1  
54863       1    0  
54864       1    1  
54865       0    1  
54866       1    1  

[54867 rows x 19 columns]

In [23]:
offers_profile_complete.rename(columns={'reward_x': 'reward_received', 'reward_y': 'reward_to_receive'}, inplace=True)

In [28]:
offers_profile_complete.to_csv("processed_data/processed_offers.csv", index=False)

In [25]:
offers_profile_complete = pd.read_csv("processed_data/processed_offers.csv")

In [26]:
offers_profile_complete['offer success'] = (offers_profile_complete['offer completed'] > offers_profile_complete['offer viewed']).astype(int)

In [30]:
offers_profile_complete.drop(['Unnamed: 0', 'Unnamed: 0.1'], inplace=True, axis=1)

In [31]:
offers_profile_complete

person  offer received  offer viewed  \
0      78afa995795e4d85b5d9ceeca43f5fef               0           6.0   
1      78afa995795e4d85b5d9ceeca43f5fef             168         216.0   
2      78afa995795e4d85b5d9ceeca43f5fef             408         408.0   
3      78afa995795e4d85b5d9ceeca43f5fef             504         582.0   
4      e2127556f4f64592b11af22de27a7932               0          18.0   
...                                 ...             ...           ...   
54862  9dc1421481194dcd9400aec7c9ae6366             408         516.0   
54863  9dc1421481194dcd9400aec7c9ae6366             576         624.0   
54864  e4052622e5ba45a8b96b59aba68cf068               0           6.0   
54865  e4052622e5ba45a8b96b59aba68cf068             576           NaN   
54866  e4052622e5ba45a8b96b59aba68cf068             408         546.0   

       offer completed  reward_received                             offer  \
0                132.0              5.0  9b98b8c7a33c4b65b9aebfe6a799e6d9   
1                  NaN              NaN  5a8bc65990b245e5a138643cd4eb9837   
2                510.0             10.0  ae264e3637204a6fb9bb56bc8210ddfd   
3                510.0              5.0  f19421c1d4aa40978ebb69ca19b0e20d   
4                  NaN              NaN  2906b810c7d4411798c6938adc9daaa5   
...                ...              ...                               ...   
54862            414.0              5.0  9b98b8c7a33c4b65b9aebfe6a799e6d9   
54863            594.0             10.0  ae264e3637204a6fb9bb56bc8210ddfd   
54864             54.0              3.0  2298d6c36e964ae4a3e7e9706d1fb8c2   
54865              NaN              NaN  3f207df678b143eea3cee63160fa8bed   
54866            480.0              5.0  f19421c1d4aa40978ebb69ca19b0e20d   

      gender  age  became_member_on    income  reward_to_receive  difficulty  \
0          F   75          20170509  100000.0                  5           5   
1          F   75          20170509  100000.0                  0           0   
2          F   75          20170509  100000.0                 10          10   
3          F   75          20170509  100000.0                  5           5   
4          M   68          20180426   70000.0                  2          10   
...      ...  ...               ...       ...                ...         ...   
54862      F   83          20160307   50000.0                  5           5   
54863      F   83          20160307   50000.0                 10          10   
54864      F   62          20170722   82000.0                  3           7   
54865      F   62          20170722   82000.0                  0           0   
54866      F   62          20170722   82000.0                  5           5   

       duration     offer_type  email  mobile  social  web  offer success  
0             7           bogo      1       1       0    1              1  
1             3  informational      1       1       1    0              0  
2             7           bogo      1       1       1    0              1  
3             5           bogo      1       1       1    1              0  
4             7       discount      1       1       0    1              0  
...         ...            ...    ...     ...     ...  ...            ...  
54862         7           bogo      1       1       0    1              0  
54863         7           bogo      1       1       1    0              0  
54864         7       discount      1       1       1    1              1  
54865         4  informational      1       1       0    1              0  
54866         5           bogo      1       1       1    1              0  

[54867 rows x 19 columns]

In [32]:
offers_profile_complete.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 54867 entries, 0 to 54866
Data columns (total 19 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   person             54867 non-null  object 
 1   offer received     54867 non-null  int64  
 2   offer viewed       41380 non-null  float64
 3   offer completed    26936 non-null  float64
 4   reward_received    26936 non-null  float64
 5   offer              54867 non-null  object 
 6   gender             54867 non-null  object 
 7   age                54867 non-null  int64  
 8   became_member_on   54867 non-null  int64  
 9   income             54867 non-null  float64
 10  reward_to_receive  54867 non-null  int64  
 11  difficulty         54867 non-null  int64  
 12  duration           54867 non-null  int64  
 13  offer_type         54867 non-null  object 
 14  email              54867 non-null  int64  
 15  mobile             54867 non-null  int64  
 16  social             548

In [33]:
offers_profile_complete.describe()

offer received  offer viewed  offer completed  reward_received  \
count    54867.000000  41380.000000     26936.000000     26936.000000   
mean       357.840888    380.815853       422.947876         4.953519   
std        191.420350    194.728072       187.200591         2.908287   
min          0.000000      0.000000         0.000000         2.000000   
25%        168.000000    204.000000       306.000000         2.000000   
50%        408.000000    414.000000       456.000000         5.000000   
75%        504.000000    540.000000       576.000000         5.000000   
max        576.000000    714.000000       714.000000        10.000000   

                age  became_member_on         income  reward_to_receive  \
count  54867.000000      5.486700e+04   54867.000000       54867.000000   
mean      54.346693      2.016691e+07   65393.843294           4.209197   
std       17.393127      1.189536e+04   21622.626419           3.405811   
min       18.000000      2.013073e+07   30000.000000           0.000000   
25%       42.000000      2.016052e+07   49000.000000           2.000000   
50%       55.000000      2.017080e+07   63000.000000           5.000000   
75%       66.000000      2.017123e+07   80000.000000           5.000000   
max      101.000000      2.018073e+07  120000.000000          10.000000   

         difficulty      duration    email        mobile        social  \
count  54867.000000  54867.000000  54867.0  54867.000000  54867.000000   
mean       7.709169      6.504730      1.0      0.899849      0.602165   
std        5.532891      2.205147      0.0      0.300204      0.489455   
min        0.000000      3.000000      1.0      0.000000      0.000000   
25%        5.000000      5.000000      1.0      1.000000      0.000000   
50%       10.000000      7.000000      1.0      1.000000      1.000000   
75%       10.000000      7.000000      1.0      1.000000      1.000000   
max       20.000000     10.000000      1.0      1.000000      1.000000   

               web  offer success  
count  54867.00000   54867.000000  
mean       0.79864       0.300053  
std        0.40102       0.458285  
min        0.00000       0.000000  
25%        1.00000       0.000000  
50%        1.00000       0.000000  
75%        1.00000       1.000000  
max        1.00000       1.000000

In [35]:
offers_profile_complete['age bin'] = pd.cut(offers_profile_complete['age'], bins=5)
offers_profile_complete

person  offer received  offer viewed  \
0      78afa995795e4d85b5d9ceeca43f5fef               0           6.0   
1      78afa995795e4d85b5d9ceeca43f5fef             168         216.0   
2      78afa995795e4d85b5d9ceeca43f5fef             408         408.0   
3      78afa995795e4d85b5d9ceeca43f5fef             504         582.0   
4      e2127556f4f64592b11af22de27a7932               0          18.0   
...                                 ...             ...           ...   
54862  9dc1421481194dcd9400aec7c9ae6366             408         516.0   
54863  9dc1421481194dcd9400aec7c9ae6366             576         624.0   
54864  e4052622e5ba45a8b96b59aba68cf068               0           6.0   
54865  e4052622e5ba45a8b96b59aba68cf068             576           NaN   
54866  e4052622e5ba45a8b96b59aba68cf068             408         546.0   

       offer completed  reward_received                             offer  \
0                132.0              5.0  9b98b8c7a33c4b65b9aebfe6a799e6d9   
1                  NaN              NaN  5a8bc65990b245e5a138643cd4eb9837   
2                510.0             10.0  ae264e3637204a6fb9bb56bc8210ddfd   
3                510.0              5.0  f19421c1d4aa40978ebb69ca19b0e20d   
4                  NaN              NaN  2906b810c7d4411798c6938adc9daaa5   
...                ...              ...                               ...   
54862            414.0              5.0  9b98b8c7a33c4b65b9aebfe6a799e6d9   
54863            594.0             10.0  ae264e3637204a6fb9bb56bc8210ddfd   
54864             54.0              3.0  2298d6c36e964ae4a3e7e9706d1fb8c2   
54865              NaN              NaN  3f207df678b143eea3cee63160fa8bed   
54866            480.0              5.0  f19421c1d4aa40978ebb69ca19b0e20d   

      gender  age  became_member_on    income  reward_to_receive  difficulty  \
0          F   75          20170509  100000.0                  5           5   
1          F   75          20170509  100000.0                  0           0   
2          F   75          20170509  100000.0                 10          10   
3          F   75          20170509  100000.0                  5           5   
4          M   68          20180426   70000.0                  2          10   
...      ...  ...               ...       ...                ...         ...   
54862      F   83          20160307   50000.0                  5           5   
54863      F   83          20160307   50000.0                 10          10   
54864      F   62          20170722   82000.0                  3           7   
54865      F   62          20170722   82000.0                  0           0   
54866      F   62          20170722   82000.0                  5           5   

       duration     offer_type  email  mobile  social  web  offer success  \
0             7           bogo      1       1       0    1              1   
1             3  informational      1       1       1    0              0   
2             7           bogo      1       1       1    0              1   
3             5           bogo      1       1       1    1              0   
4             7       discount      1       1       0    1              0   
...         ...            ...    ...     ...     ...  ...            ...   
54862         7           bogo      1       1       0    1              0   
54863         7           bogo      1       1       1    0              0   
54864         7       discount      1       1       1    1              1   
54865         4  informational      1       1       0    1              0   
54866         5           bogo      1       1       1    1              0   

            age bin  
0      (67.8, 84.4]  
1      (67.8, 84.4]  
2      (67.8, 84.4]  
3      (67.8, 84.4]  
4      (67.8, 84.4]  
...             ...  
54862  (67.8, 84.4]  
54863  (67.8, 84.4]  
54864  (51.2, 67.8]  
54865  (51.2, 67.8]  
54866  (51.2, 67.8]  

[54867 rows x 20 columns]

In [39]:
px.histogram(offers_profile_complete, x="gender")

In [41]:
offers_profile_complete['age bin'] = offers_profile_complete['age bin'].astype(str)
px.histogram(offers_profile_complete, x="age bin")

In [42]:
px.histogram(offers_profile_complete, x="offer_type")

In [53]:
data = dict(
    number=[offers_profile_complete['offer received'].count(), offers_profile_complete['offer viewed'].count(), offers_profile_complete['offer completed'].count(),  offers_profile_complete['offer success'].sum()],
    stage=["Offers Received", "Offers Viewed", "Offers Completed", "Offers Completed with Success"])

px.funnel(data, x='number', y='stage')

In [59]:
stages = ["Offers Received", "Offers Viewed", "Offers Completed", "Offers Completed with Success"]
df_bogo = pd.DataFrame(dict(number=[offers_profile_complete.loc[offers_profile_complete['offer_type'] == 'bogo','offer received'].count(), offers_profile_complete.loc[offers_profile_complete['offer_type'] == 'bogo', 'offer viewed'].count(), offers_profile_complete.loc[offers_profile_complete['offer_type'] == 'bogo', 'offer completed'].count(),  offers_profile_complete.loc[offers_profile_complete['offer_type'] == 'bogo', 'offer success'].sum()], stage=stages))
df_bogo['offer_type'] = 'bogo'

In [60]:
df_informational = pd.DataFrame(dict(number=[offers_profile_complete.loc[offers_profile_complete['offer_type'] == 'informational','offer received'].count(), offers_profile_complete.loc[offers_profile_complete['offer_type'] == 'informational', 'offer viewed'].count(), offers_profile_complete.loc[offers_profile_complete['offer_type'] == 'informational', 'offer completed'].count(),  offers_profile_complete.loc[offers_profile_complete['offer_type'] == 'informational', 'offer success'].sum()], stage=stages))
df_informational['offer_type'] = 'informational'

In [61]:
df_discount = pd.DataFrame(dict(number=[offers_profile_complete.loc[offers_profile_complete['offer_type'] == 'discount','offer received'].count(), offers_profile_complete.loc[offers_profile_complete['offer_type'] == 'discount', 'offer viewed'].count(), offers_profile_complete.loc[offers_profile_complete['offer_type'] == 'discount', 'offer completed'].count(),  offers_profile_complete.loc[offers_profile_complete['offer_type'] == 'discount', 'offer success'].sum()], stage=stages))
df_discount['offer_type'] = 'discount'

In [63]:
data = pd.concat([df_bogo, df_discount, df_informational], axis=0)
px.funnel(data, x='number', y='stage', color='offer_type')

In [65]:
offers_profile_complete['income_bin'] = pd.cut(offers_profile_complete['income'], bins=5).astype(str)

In [68]:
px.histogram(offers_profile_complete, x="income_bin")

In [67]:
px.treemap(offers_profile_complete, path=['offer_type', 'income_bin', 'gender'], values='offer success')